# Exécution de Streamlit depuis Colab

In [ ]:
!pip install -q streamlit

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.4/8.4 MB 13.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 195.4/195.4 kB 17.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.8/4.8 MB 33.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 83.0/83.0 kB 9.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.7/62.7 kB 7.6 MB/s eta 0:00:00


In [ ]:
%%writefile app.py

import streamlit as st
st.write('Hello, *World!* :sunglasses:')

Writing app.py


In [ ]:
!npm install localtunnel

npm WARN saveError ENOENT: no such file or directory, open '/content/package.json'
npm notice created a lockfile as package-lock.json. You should commit this file.
npm WARN enoent ENOENT: no such file or directory, open '/content/package.json'
npm WARN content No description
npm WARN content No repository field.
npm WARN content No README data
npm WARN content No license field.

+ localtunnel@2.0.2
added 22 packages from 22 contributors and audited 22 packages in 2.037s

3 packages are looking for funding
  run `npm fund` for details

found 1 moderate severity vulnerability
  run `npm audit fix` to fix them, or `npm audit` for details


In [ ]:
!streamlit run app.py --server.address=localhost &>/content/logs.txt &

In [ ]:
!npx localtunnel --port 8501

npx: installed 22 in 1.752s
your url is: https://fuzzy-files-invent.loca.lt
^C


In [ ]:
import urllib
print("Password/Enpoint IP for localtunnel is:",urllib.request.urlopen('https://ipv4.icanhazip.com').read().decode('utf8').strip("\n"))

Password/Enpoint IP for localtunnel is: 34.106.110.229


# Géocodage

In [ ]:
# spécifique colab
!pip install rasterio

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 20.6/20.6 MB 59.3 MB/s eta 0:00:00


In [ ]:
import requests
from io import BytesIO
import json
import rasterio
from PIL import Image, ImageOps
import plotly.express as px
import geopandas as gpd
import shapely

In [ ]:
adresse = '103 rue du chateau, Boulogne'
request_wxs = 'https://wxs.ign.fr/essentiels/geoportail/geocodage/rest/0.1/search?q={}&index=address&limit=1&returntruegeometry=false'.format(
    adresse
)
response_wxs = requests.get(request_wxs).content
adresses = json.load(BytesIO(response_wxs))

In [ ]:
adresses

{'type': 'FeatureCollection',
 'features': [{'type': 'Feature',
   'properties': {'label': '103 Rue du Château 92100 Boulogne-Billancourt',
    'score': 0.6920095693779904,
    'housenumber': '103',
    'id': '92012_1425_00103',
    'name': '103 Rue du Château',
    'postcode': '92100',
    'citycode': '92012',
    'x': 644318.23,
    'y': 6860531.39,
    'city': 'Boulogne-Billancourt',
    'context': '92, Hauts-de-Seine, Île-de-France',
    'type': 'housenumber',
    'importance': 0.77,
    'street': 'Rue du Château',
    '_score': 0.6920095693779904,
    '_type': 'ban'},
   'geometry': {'type': 'Point', 'coordinates': [2.241316, 48.842423]}}]}

In [ ]:
X0 = adresses['features'][0]['properties']['x']
Y0 = adresses['features'][0]['properties']['y']
X_size = 1000
Y_size = 1000
coords_scale = 0.2

raster_transform = rasterio.transform.Affine(coords_scale, 0.0, X0,
                          0.0, -coords_scale, Y0 + coords_scale*Y_size)
xmin, ymax = raster_transform*(0, 0)
xmax, ymin = raster_transform*(X_size, Y_size)
bounds = gpd.GeoDataFrame(
    {'Nom': ['name1', 'name2'],
     'geometry': [shapely.geometry.Point(xmin, ymin), shapely.geometry.Point(xmax, ymax)]},
    crs = 'EPSG:2154')
bounds

Nom                        geometry
0  name1  POINT (644318.230 6860531.390)
1  name2  POINT (644518.230 6860731.390)

In [ ]:
[bounds.geometry[0].y, bounds.geometry[0].x]

[6862318.21, 648244.83]

In [ ]:
request_wms = 'https://data.geopf.fr/wms-r?LAYERS=ORTHOIMAGERY.ORTHOPHOTOS&FORMAT=image/tiff&SERVICE=WMS&VERSION=1.3.0&REQUEST=GetMap&STYLES=&CRS=EPSG:2154&BBOX={},{},{},{}&WIDTH={}&HEIGHT={}'.format(
   bounds.geometry[0].x, bounds.geometry[0].y, bounds.geometry[1].x, bounds.geometry[1].y, X_size, Y_size)
response_wms = requests.get(request_wms).content
orthophoto = Image.open(BytesIO(response_wms))

In [ ]:
px.imshow(orthophoto)

# Détection

## Librairies et données

In [ ]:
# partie spécifique Google Colab
!pip install tensorflow==2.15.0 rasterio plotly scikit-image shapely
!pip install ultralytics==8.0.38
!pip install rasterio plotly scikit-image shapely

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 20.6/20.6 MB 44.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 278.1/278.1 kB 1.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 266.1/266.1 kB 14.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 23.7/23.7 MB 35.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 823.6/823.6 kB 44.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 14.1/14.1 MB 52.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 731.7/731.7 MB 2.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 410.6/410.6 MB 2.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 121.6/121.6 MB 7.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.5/56.5 MB 11.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 124.2/124.2 MB 8.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 196.0/196.0 MB 6.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━

In [ ]:
import numpy as np
import glob
import plotly.express as px
import plotly.graph_objs as go
import cv2
import pandas as pd
import tqdm
from datetime import date
from google.colab import drive
import random
import matplotlib.pyplot as plt
import os
import math
from pathlib import Path
import shutil
from PIL import Image, ImageOps
from io import BytesIO
import requests

import geopandas as gpd
import rasterio
import rasterio.mask
import shapely
import skimage as ski
from skimage.measure import find_contours, approximate_polygon, subdivide_polygon, label

from sklearn.model_selection import train_test_split
from sklearn.cluster import KMeans
from sklearn.base import BaseEstimator, ClassifierMixin
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import GridSearchCV
from sklearn.metrics import mean_absolute_error, accuracy_score
from sklearn.base import TransformerMixin, BaseEstimator
from sklearn.pipeline import Pipeline

import tensorflow as tf
from tensorflow import image as tf_image
from tensorflow import data as tf_data
from tensorflow import io as tf_io

import keras
from keras import layers, Model, backend
from keras.layers import Input, Rescaling, Dense, Dropout, Flatten, Conv2D, Conv2DTranspose, \
MaxPooling2D, AveragePooling2D, SpatialDropout2D, BatchNormalization, Activation, SeparableConv2D, \
UpSampling2D, GlobalAveragePooling2D
from keras.models import Sequential, load_model
from keras.optimizers import Adam
from keras.callbacks import ReduceLROnPlateau, ModelCheckpoint
from keras.utils import load_img, img_to_array, array_to_img

from ultralytics import YOLO
import torch

In [ ]:
# partie spécifique Google Colab
!mkdir -p /content/data/decoupe_final
!cp /content/drive/MyDrive/data/DST/df_decoupe_final.csv /content/data/decoupe_final/df_decoupe_final.csv
!unzip /content/drive/MyDrive/data/DST/decoupe_final.zip -d /content/data/decoupe_final

Le flux de sortie a été tronqué et ne contient que les 5000 dernières lignes.
 extracting: /content/data/decoupe_final/decoupe_final/69-2020_8_834400.0_22_6508200.0_33.cpg  
  inflating: /content/data/decoupe_final/decoupe_final/69-2020_8_834400.0_22_6508200.0_33.dbf  
  inflating: /content/data/decoupe_final/decoupe_final/69-2020_8_834400.0_22_6508200.0_33.jp2  
  inflating: /content/data/decoupe_final/decoupe_final/69-2020_8_834400.0_22_6508200.0_33.prj  
  inflating: /content/data/decoupe_final/decoupe_final/69-2020_8_834400.0_22_6508200.0_33.shp  
  inflating: /content/data/decoupe_final/decoupe_final/69-2020_8_834400.0_22_6508200.0_33.shx  
 extracting: /content/data/decoupe_final/decoupe_final/69-2020_8_834400.0_22_6508200.0_33_data.jpg  
  inflating: /content/data/decoupe_final/decoupe_final/69-2020_8_834400.0_22_6508200.0_33_data.jpg.aux.xml  
  inflating: /content/data/decoupe_final/decoupe_final/69-2020_8_834400.0_22_6508200.0_33_label.png  
  inflating: /content/data/decoupe

In [ ]:
data_path = '/content/data/decoupe_final'
images_path = '/content/data/decoupe_final/decoupe_final'
df_decoupe = pd.read_csv(data_path + '/df_decoupe_final.csv')
df_decoupe.head()

dalle_X  dalle_Y         X          Y  X_size  ...  \
0        0        0  825000.0  6509800.0    1000  ...   
1        0        1  825000.0  6509600.0    1000  ...   
2        0        2  825000.0  6509400.0    1000  ...   
3        0        3  825000.0  6509200.0    1000  ...   
4        0        4  825000.0  6509000.0    1000  ...   

                                  fichier_mask  \
0   69-2020_0_825000.0_0_6509800.0_0_label.png   
1   69-2020_1_825000.0_0_6509600.0_0_label.png   
2   69-2020_2_825000.0_0_6509400.0_4_label.png   
3   69-2020_3_825000.0_0_6509200.0_4_label.png   
4  69-2020_4_825000.0_0_6509000.0_19_label.png   

                          fichier_shapes formes multi erreur  
0   69-2020_0_825000.0_0_6509800.0_0.shp      0     0      0  
1   69-2020_1_825000.0_0_6509600.0_0.shp      0     0      0  
2   69-2020_2_825000.0_0_6509400.0_4.shp      4     0      0  
3   69-2020_3_825000.0_0_6509200.0_4.shp      4     0      0  
4  69-2020_4_825000.0_0_6509000.0_19.shp     19     0      0  

[5 rows x 13 columns]

## Fonctions

In [ ]:
def calcul_ious_shapes(shapes_1_ext, shapes_2_ext, seuil_iou = 0):
  '''
  fonction qui calcule l'IoU des shapes_1_ext en cherchant à rapprocher les shapes_2_ext
  renvoie la liste des ious calculés
  '''
  ious = []
  rapprochements = []
  selected_intersections = []
  for i in range(len(shapes_1_ext)):
    shape_1 = shapely.Polygon(shapes_1_ext[i])
    unions = []
    unions.append(shape_1)
    intersections = []
    for j in range(len(shapes_2_ext)):
      shape_2 = shapely.Polygon(shapes_2_ext[j])
      if shape_2 is not None:
        if shape_1.intersects(shape_2):
          intersection = shape_1.intersection(shape_2)
          intersections.append(intersection)
          unions.append(shape_2)
    if len(intersections) > 0:
      all_intersections = gpd.GeoSeries(intersections, crs = 2154).unary_union
      intersection_area = shapely.area(all_intersections)
    else:
      intersection_area = 0
    union_area = shapely.area(gpd.GeoSeries(unions, crs = 2154).unary_union)
    if union_area == 0:
      ious.append(0)
    else:
      iou = intersection_area/union_area
      ious.append(iou)
      if len(intersections) > 0 and iou > seuil_iou:
        selected_intersections.append(all_intersections)
    rapprochements.append(len(intersections))
  return ious, rapprochements, selected_intersections

In [ ]:
def isInMap(xrange, yrange, bounds = False):
    '''
    fonction qui renvoie une autre fonction permettant de tester si une forme
    est à l'intérieur d'un restangle défini par xrange, yrange
    si l'argument "bounds" est mis à True, la fonction renvoyée réalise le test sur la base de l'emprise rectangulaire de la forme
    sinon, la fonction renvoyée réalise le test sur la base du centroïd
    l'argument "bounds" est à False par défaut
    '''
    def my_function(polynom):
        if bounds:
            minx, miny, maxx, maxy = polynom.bounds
        else:
            centroid_x, centroid_y = polynom.centroid.x, polynom.centroid.y
            minx, miny, maxx, maxy = centroid_x, centroid_y, centroid_x, centroid_y
        if xrange[0] < minx and xrange[1] > maxx and yrange[0] < miny and yrange[1] > maxy:
            return(True)
        else:
            return(False)
    return my_function

In [ ]:
def affiche_contours(
    image, predict_function, model, size_model, coord_transform, gdf_shapes_ref, resolution_target = (1000, 1000),
    seuil = 0.05, seuil_iou = 0.01, delta_only = False,
    seuil_area = 10,
    tolerance_polygone = 0.1):
  '''
  fonction qui calcule les IoU des formes prédites par rapport à des formes de référence
  utilise les mêmes arguements que compare_ligne, avec en plus :
  - predict_function : fonction qui prend en argument le triplet (image, model, seuil) et qui renvoie une liste de prévisions du modèle "model" sous forme
  de masque numpy.array avec les dimensions correspondant au paramètre "resolution_model", pour le seuil de détection "seuil"
  /!\ predict_function doit pouvoir faire l'inférence sur l'image et non pas sur le chemin file_name
  - image : array de l'image sur laquelle faire la prédiction
  - seuil_iou : les formes avec un IoU inférieur sont affichées en rouge
  - delta_only : si True, n'affiche que les formes en rouge
  - coord_transform : transformation affine pour passer des pixels aux coordonnées géographiques cible
  - gdf_shapes_ref : fichier de shapefiles à utiliser pour la comparaison des formes prédites > par défaut, on compare par rapport aux formes du df_decoupe
  renvoie :
  - geoSeries avec les formes prédites, crs 2154, avec uniquement les contours
  - geoSeries avec les formes de réference, crs 2154, avec uniquement les contours, et en fusionnant les formes adjacentes
  - shapes_pred_ious
  - shapes_ref_ious
  - le calcul de l'iou "pixel par pixel"
  '''

  # Prévision
  prev_masks = predict_function(image, model, size_model, seuil)

  # Contours prédiction
  mask_contours = []
  for prev_mask in prev_masks:
    prev_mask_resized = tf.squeeze(tf_image.resize(images = np.expand_dims(prev_mask, -1), size = resolution_target, method = 'nearest'))
    mask_padded = np.pad(prev_mask_resized, ((1, 1),(1, 1)), mode = 'constant', constant_values = 0)
    mask_contours += ski.measure.find_contours(image = mask_padded == 1)

  # utilisation des informations raster pour les coordonnées
  X0, Y0, coords_scale = coord_transform
  raster_transform = rasterio.transform.Affine(coords_scale, 0.0, X0,
                            0.0, -coords_scale, Y0 + coords_scale*resolution_target[1])
  bounds = rasterio.coords.BoundingBox(X0, Y0, X0 + coords_scale*resolution_target[0], Y0 + coords_scale*resolution_target[1])

  # Shapes référence
  gdf_shapes_ref_copy = gdf_shapes_ref.copy()
  # on enlève les shapes extérieurs à la dalle pour diminuer le volume de données inutiles
  img_bound = shapely.Polygon(((bounds.left, bounds.bottom), (bounds.right, bounds.bottom), (bounds.right, bounds.top), (bounds.left, bounds.top), (bounds.left, bounds.bottom)))
  try:
    gdf_shapes_ref_copy['geometry'] = gdf_shapes_ref_copy['geometry'].intersection(img_bound)
    gdf_shapes_ref_copy = gdf_shapes_ref_copy[
      ~(gdf_shapes_ref_copy['geometry'].isna() | gdf_shapes_ref_copy['geometry'].is_empty)]
  except:
    # si erreur, on fait un test simple
    gdf_shapes_ref_copy = gdf_shapes_ref_copy[gdf_shapes_ref_copy['geometry'].apply(isInMap([bounds.left, bounds.right], [bounds.bottom, bounds.top], False))]

  # Shapes prédiction
  raster_transformer = rasterio.transform.AffineTransformer(raster_transform)
  shapes_xy = []
  shapes_predict = []
  # parcours de tous les contours prédits
  for contour in mask_contours:
    # on crée le polygone
    polygon = approximate_polygon(contour, tolerance = tolerance_polygone)
    # on tranforme en coordonnées
    xy_polygon = raster_transformer.xy(polygon[:,0], polygon[:,1])
    shapes_xy.append(xy_polygon)
    # on crée le polygone
    shapes_predict.append(shapely.Polygon(np.array(xy_polygon).transpose()))
  # on filtre les surface trop petites
  shapes_predict = [shape for shape in shapes_predict if shapely.area(shape) > seuil_area]
  # Ajout des trous dans les shapes prédiction
  shapes_predict_holes = []
  shapes_holes = []
  for shape_a in shapes_predict:
    if shape_a not in shapes_holes:
      shape_a_holes = []
      for shape_b in shapes_predict:
        if shape_a.contains_properly(shape_b):
          shape_a_holes.append(shape_b.exterior)
          shapes_holes.append(shape_b)
      if len(shape_a_holes) > 0:
        shapes_predict_holes.append(shapely.Polygon(shape_a.exterior, holes = shape_a_holes))
      else:
        shapes_predict_holes.append(shape_a)
  gdf_shapes_predict = gpd.GeoDataFrame(geometry = gpd.GeoSeries(shapes_predict_holes, crs=2154), crs=2154)

  # Intersection et IoUs
  shapes_ref = gdf_shapes_ref_copy['geometry'].exterior
  shapes_ref = [shape for shape in shapes_ref if shape is not None]
  shapes_predict = gdf_shapes_predict['geometry'].exterior
  shapes_predict = [shape for shape in shapes_predict if shape is not None]
  # iou des prédictions
  shapes_pred_ious, shapes_pred_rapprochements, _ = calcul_ious_shapes(shapes_predict, shapes_ref)
  # iou des réferences
  shapes_ref_ious, shapes_ref_rapprochements, _ = calcul_ious_shapes(shapes_ref, shapes_predict)

  # génération du graphique
  nb_formes = len(shapes_ref)
  fig = px.imshow(
      #cv2.flip(raster_data, 0),
      ImageOps.flip(image),
      x = np.linspace(bounds.left, bounds.right, resolution_target[0]),
      y = np.linspace(bounds.bottom, bounds.top, resolution_target[1]),
      title = '{} bâtiments référence<br>{} zones détectées'.format(
          str(nb_formes),
          np.sum((np.array(shapes_pred_ious) <= seuil_iou) & (np.array(shapes_pred_rapprochements) == 0))),
      origin = 'lower')
  # ajout des formes
  shape_traces_to_plot = []
  if not delta_only:
    # formes de référence
    for i, (shape, iou, rapprochement) in enumerate(zip(shapes_ref, shapes_ref_ious,
                                                        shapes_ref_rapprochements)):
      list_x, list_y = shape.xy
      shape_traces_to_plot.append(
          go.Scatter(
              x = np.array(list_x),
              y = np.array(list_y),
              line = dict(color='black', width=1),
              mode = 'lines',
              fill = 'toself',
              fillcolor = '#80b1d3',
              opacity = 0.4,
              text = 'iou référence: {}<br>{} prédictions rapprochées'.format(iou, rapprochement),
              hoverinfo = 'text',
              name = 'référence',
              legendgroup = 'référence',
              showlegend = (i==0)))
  # formes prédites
  i_pred = 0
  i_pred_delta = 0
  for i, (shape, iou, rapprochement) in enumerate(zip(shapes_predict, shapes_pred_ious, shapes_pred_rapprochements)):
    list_x, list_y = shape.simplify(1).xy
    if iou <= seuil_iou:
      shape_traces_to_plot.append(
        go.Scatter(
            x = np.array(list_x),
            y = np.array(list_y),
            line = dict(color='black', width=1),
            mode = 'lines',
            fill = 'toself',
            fillcolor = 'red',
            opacity = 0.4,
            text = 'iou prédiction: {}'.format(iou),
            hoverinfo = 'text',
            name = 'écart',
            legendgroup = 'écart',
            showlegend = (i_pred_delta==0)))
      i_pred_delta += 1
    elif not delta_only:
      shape_traces_to_plot.append(
        go.Scatter(
            x = np.array(list_x),
            y = np.array(list_y),
            line = dict(color='black', width=1),
            mode = 'lines',
            fill = 'toself',
            fillcolor = '#ffed6f',
            opacity = 0.4,
            text = 'iou prédiction: {}<br>{} bâtiments rapprochés'.format(iou, rapprochement),
            hoverinfo = 'text',
            name = 'prédiction',
            legendgroup = 'prédiction',
            showlegend = (i_pred==0)))
      i_pred += 1

  fig.add_traces(shape_traces_to_plot)
  # mise en forme
  fig.update_layout(
      xaxis=dict(title='X en Lambert93'),
      yaxis=dict(title='Y en Lambert93'),
      plot_bgcolor='white',
      height = 900,
      width = 900)

  return shapes_predict, shapes_ref, shapes_pred_ious, shapes_ref_ious, shapes_pred_rapprochements, shapes_ref_rapprochements, fig


In [ ]:
def predict_YOLOv8(image, model, size_model = 512, seuil = 0.01):
  '''
  on ne prédit que la classe "0", bâtiments
  '''
  res = model.predict(image, save = False, classes = [0], imgsz = size_model, conf = seuil, verbose=False)
  if len(res[0]) > 0:
    mask = np.sum(res[0].masks.data.cpu().numpy(), 0)
    mask = np.clip(mask, 0, 1)
  else:
    mask = [np.zeros((size_model, size_model))]
  return [mask]

## Géodétection

In [ ]:
SIZE_YOLO = 512
model_YOLO = YOLO('/content/drive/MyDrive/DataScientest/YOLO/YOLOv8_20240124/weights/best.pt')


In [ ]:
df = df_decoupe
index_l = 7377
chemin_images = images_path + '/'
X_size = df.iloc[index_l]['X_size']
Y_size = df.iloc[index_l]['Y_size']
# X_size = Y_size = 1000
coords_scale = 0.2
# X0 = df.iloc[index_l]['X']
# Y0 = df.iloc[index_l]['Y']
X0 = 644326.03
Y0 = 6860333.65

raster_transform = rasterio.transform.Affine(coords_scale, 0.0, X0,
                          0.0, coords_scale, Y0)
xmin, ymin = raster_transform*(0, 0)
xmax, ymax = raster_transform*(X_size, Y_size)
request_wms = 'https://data.geopf.fr/wms-r?LAYERS=HR.ORTHOIMAGERY.ORTHOPHOTOS&FORMAT=image/tiff&SERVICE=WMS&VERSION=1.3.0&REQUEST=GetMap&STYLES=&CRS=EPSG:2154&BBOX={},{},{},{}&WIDTH={}&HEIGHT={}'.format(
   xmin, ymin, xmax, ymax, X_size, Y_size)
response_wms = requests.get(request_wms).content
orthophoto = Image.open(BytesIO(response_wms))
#prev_data = model_YOLO.predict(orthophoto, save = False, classes = [0], imgsz = SIZE_YOLO, conf = 0.01, verbose=False)
#prev_data = predict_YOLOv8(orthophoto, model_YOLO, size_model = SIZE_YOLO)

bounds = gpd.GeoDataFrame(
    {'Nom': ['name1', 'name2'],
     'geometry': [shapely.geometry.Point(xmin, ymin), shapely.geometry.Point(xmax, ymax)]},
    crs = 'EPSG:2154')
bounds = bounds.to_crs('EPSG:4326')
'''
ancienne URL
request_wfs = 'https://wxs.ign.fr/parcellaire/geoportail/wfs?SERVICE=WFS&VERSION=2.0.0&REQUEST=GetFeature&typename=CADASTRALPARCELS.PARCELLAIRE_EXPRESS:batiment&outputformat=application/json&BBOX={},{},{},{}'.format(
    bounds.geometry[0].y, bounds.geometry[0].x, bounds.geometry[1].y, bounds.geometry[1].x)
'''
request_wfs = 'https://data.geopf.fr/wfs?SERVICE=WFS&VERSION=2.0.0&REQUEST=GetFeature&typename=CADASTRALPARCELS.PARCELLAIRE_EXPRESS:batiment&outputformat=application/json&BBOX={},{},{},{}'.format(
    bounds.geometry[0].y, bounds.geometry[0].x, bounds.geometry[1].y, bounds.geometry[1].x)

response_wfs = requests.get(request_wfs)
gdf_cadastre = gpd.GeoDataFrame.from_features(response_wfs.json()['features'])
if gdf_cadastre.shape[0]>0 :
    gdf_cadastre = gdf_cadastre.set_crs('EPSG:4326').to_crs('EPSG:2154')
    gdf_cadastre['geometry'] = gdf_cadastre['geometry'].make_valid()
    gdf_cadastre = gdf_cadastre.explode(index_parts = False)
    gdf_cadastre = gdf_cadastre[gdf_cadastre['geometry'].geom_type.isin(['Polygon', 'MultiPolygon'])]


In [ ]:
shapes_predict, shapes_ref, _, _, _, _, fig = affiche_contours(
    orthophoto, predict_YOLOv8, model_YOLO, SIZE_YOLO, (X0, Y0, coords_scale), gdf_shapes_ref = gdf_cadastre,
    resolution_target = (X_size, Y_size),
    seuil = 0.05, seuil_iou = 0.01, delta_only = False,
    seuil_area = 10,
    tolerance_polygone = 0.1)
fig.show()

In [ ]:
new_fig_data = [item for item in fig.data if item.name not in ['prédiction', 'écart']]
new_fig_data

[Image({
     'dx': 0.2002002001972869,
     'dy': 0.20020020008087158,
     'hovertemplate': 'x: %{x}<br>y: %{y}<br>color: [%{z[0]}, %{z[1]}, %{z[2]}]<extra></extra>',
     'name': '0',
     'source': ('data:image/png;base64,iVBORw0K' ... 'j/C9Xlqe4HrGuoAAAAAElFTkSuQmCC'),
     'x0': 644326.03,
     'xaxis': 'x',
     'y0': 6860333.65,
     'yaxis': 'y'
 }),
 Scatter({
     'fill': 'toself',
     'fillcolor': '#80b1d3',
     'hoverinfo': 'text',
     'legendgroup': 'référence',
     'line': {'color': 'black', 'width': 1},
     'mode': 'lines',
     'name': 'référence',
     'opacity': 0.4,
     'showlegend': True,
     'text': 'iou référence: 0.05987158971291256<br>1 prédictions rapprochées',
     'x': array([ 6.4443e+05,  6.4445e+05,  6.4445e+05,  6.4445e+05,  6.4443e+05,
                  6.4443e+05,  6.4443e+05]),
     'y': array([ 6.8605e+06,  6.8605e+06,  6.8605e+06,  6.8605e+06,  6.8605e+06,
                  6.8605e+06,  6.8605e+06])
 }),
 Scatter({
     'fill': 'toself',
     

In [ ]:
fig.data = new_fig_data
fig.show()

In [ ]:
import tensorflow as tf
RESOLUTION = (512, 512)

img_reduite = tf.image.resize(images = orthophoto, size = RESOLUTION)

In [ ]:
img_reduite

<tf.Tensor: shape=(512, 512, 3), dtype=float32, numpy=
array([[[     105.73,      115.73,      123.78],
        [     135.39,      143.64,      150.19],
        [     134.64,       142.3,      149.16],
        ...,
        [     152.14,      155.94,      158.14],
        [     156.25,      160.25,      161.25],
        [     156.18,      160.18,      160.41]],

       [[     137.82,      150.14,      157.91],
        [     148.74,      158.74,      163.31],
        [     157.38,      167.24,      171.81],
        ...,
        [     154.66,      158.66,      160.87],
        [     156.96,      160.96,      161.77],
        [     153.27,      157.27,      157.45]],

       [[      151.7,      164.29,      170.57],
        [      153.1,       165.6,      168.67],
        [     156.81,       169.2,      171.81],
        ...,
        [     150.82,      154.68,      157.06],
        [      153.1,       157.1,       158.1],
        [     153.09,      157.09,      157.36]],

       ...,

     